# Импорт необходимых библиотек

In [1]:
!pip install deeppavlov emoji

In [2]:
!pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu124
!pip install tensorflow==2.15.1

Looking in indexes: https://download.pytorch.org/whl/cu124


In [3]:
!export PATH=/usr/local/cuda-12.4/bin:$PATH
!export LD_LIBRARY_PATH=/usr/local/cuda-12.4/lib64:$LD_LIBRARY_PATH

In [4]:
# Настройка предупреждений
import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

In [5]:
import os
import gdown
import nltk
import subprocess
import cudf.pandas
cudf.pandas.install()
import pandas as pd
import locale
import torch
from transformers import pipeline
import spacy
from torch.utils.data import DataLoader, Dataset
from concurrent.futures import ThreadPoolExecutor
import numpy as np
import tensorflow as tf
from collections import defaultdict, Counter
from textblob import TextBlob
import re
from string import punctuation
from spacy.lang.ru.stop_words import STOP_WORDS as stopwords_ru
from sklearn.feature_extraction.text import CountVectorizer
from deeppavlov import build_model, configs
from itertools import combinations
import warnings
from nltk.corpus import stopwords
from tqdm import tqdm
import emoji
import os
import gdown
import subprocess
import pandas as pd
import nltk
import torch
import spacy
import tensorflow as tf
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor
from transformers import pipeline
from spacy.lang.ru.stop_words import STOP_WORDS as stopwords_ru
from string import punctuation
from textblob import TextBlob
from collections import defaultdict, Counter
from itertools import combinations
import re
import emoji
import matplotlib.pyplot as plt

2024-07-31 14:00:19.728406: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-07-31 14:00:19.728455: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-07-31 14:00:19.729265: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-07-31 14:00:19.734681: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-07-31 14:00:20.371172: W tensorflow/compiler/tf2

# Проверка доступности GPU

In [6]:
cuda_available = torch.cuda.is_available()
num_gpus = torch.cuda.device_count()
devices = tf.config.list_physical_devices('GPU')
gpu_available = len(devices) > 0

print(f"CUDA Available: {cuda_available}")
print(f"Number of GPUs: {num_gpus}")
print(f"GPU Available: {gpu_available}")
for device in devices:
    print(f"Device: {device}")

CUDA Available: True
Number of GPUs: 1
GPU Available: False


2024-07-31 14:00:21.284061: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:08:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-07-31 14:00:21.285276: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2256] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


# Функции для загрузки файлов и установки моделей

In [7]:
def download_file_if_not_exists(file_url, output_path):
    if os.path.exists(output_path):
        print(f"Файл '{output_path}' уже существует.")
    else:
        print(f"Файл '{output_path}' не найден. Начинаю загрузку...")
        gdown.download(file_url, output_path, quiet=False)
        print(f"Файл '{output_path}' успешно загружен.")

def install_spacy_model_if_not_exists(model_name):
    try:
        result = subprocess.run(['python', '-m', 'spacy', 'info'], capture_output=True, text=True, check=True)
        if model_name in result.stdout:
            print(f"Модель {model_name} уже установлена.")
        else:
            print(f"Модель {model_name} не найдена. Устанавливаю...")
            subprocess.run(['python', '-m', 'spacy', 'download', model_name], check=True)
            print(f"Модель {model_name} успешно установлена.")
    except subprocess.CalledProcessError as e:
        print(f"Ошибка при выполнении команды: {e}")

# Загрузка необходимых ресурсов и моделей

In [8]:
nltk.download('stopwords')
install_spacy_model_if_not_exists('ru_core_news_lg')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Модель ru_core_news_lg уже установлена.


In [9]:
import os
import gdown

def download_file_if_not_exists(file_url, output_path):
    """Скачивает файл с Google Drive, если он ещё не существует в указанной директории."""
    # Проверка наличия файла
    if os.path.exists(output_path):
        print(f"Файл '{output_path}' уже существует.")
    else:
        print(f"Файл '{output_path}' не найден. Начинаю загрузку...")
        gdown.download(file_url, output_path, quiet=False)
        print(f"Файл '{output_path}' успешно загружен.")

# Указываем URL и путь к файлу
file_url = 'https://drive.google.com/uc?id=1alondqI-2IHo__mYU7KQz4Ip8ytYGHXg'
output_file_name = 'wildberries_reviews.csv'  # Укажите реальное имя файла, которое хотите сохранить
output_path = os.path.join(os.getcwd(), output_file_name)  # Полный путь к файлу

download_file_if_not_exists(file_url, output_path)


Файл '/workspace/wildberries_reviews.csv' уже существует.


# Предобработка данных

In [10]:
import pandas as pd
df_raw = pd.read_csv('wildberries_reviews.csv')
df_raw.head()
df_test = df_raw.drop(['Unnamed: 0'], axis=1)
df_test.groupby('category').count().sort_values(by='review_full_text', ascending=False)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
df = df_test
" ".join(df["review_full_text"].to_list())

'Работает хорошо. Пришло быстро, все целое на вид. Завтра буду испытывать.. Купил на квадр для поднятия отвала, установка заняла час👍 Лебёдка хорошая. Но в инструкции ни слова про сборку и крепление к машине. Всё в комплекте, есть инструкция на русском языке. Муж ещё не пробовал 👍 Пока при проверке работает нормально, а там посмотрим на сколько хватит Не комплект, нет крюка, заметил поздно, кроме возврата ничего не предложили, проверяйте комплектность внимательнее, а не так как я. При первой поездки в лес, барабан отломился когда начал намотку, а после и вообще трос зажувала! Деньги на ветер! Мужу заказала. Товар понравился. Только не доложили в комплекте одну гайку. Установил, работает. Полный комплект для установки. установили. сразу начала подозрительно хрустеть без груза. второй раз включил ее попробовать, всё, уже не отпускает. только поднимает. при нажатии на кнопку отпускания, провод задымел. сейчас будем через тех поддержку решать как то вопрос. цена не три копейки Все в компле

# Очистка и предобработка текста

In [11]:
import re
import emoji

def clean_text(text):
    def remove_emoji(text):
        return emoji.replace_emoji(text, replace='')

    def fix_spaces(text):
        text = re.sub(r'\s+', ' ', text)
        text = re.sub(r'\s*([,.!?;:])\s*', r'\1 ', text)
        text = re.sub(r'\s*-\s*', ' - ', text)
        text = re.sub(r'\s*–\s*', ' – ', text)
        text = re.sub(r'\s*—\s*', ' — ', text)
        return text.strip()

    def check_numbers(text):
        def replace_invalid_numbers(match):
            return match.group(0).replace('.', ',').replace(',', '.')
        text = re.sub(r'(\d+[.,]){2,}', replace_invalid_numbers, text)
        return text

    text = remove_emoji(text)
    text = fix_spaces(text)
    text = check_numbers(text)
    return text

# Обработка текстов

In [12]:
import spacy
import pandas as pd
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor

spacy.prefer_gpu()
nlp = spacy.load('ru_core_news_lg')

def get_segments(doc):
    segments = []
    segment_data = []
    segment = []

    for sentence in doc.sents:
        for token in sentence:
            if token.is_punct:
                if token.text in {'.', '!', '?' }:
                    if segment:
                        segments.append({
                            'text': ' '.join(segment),
                            'details': segment_data
                        })
                        segment = []
                        segment_data = []
            else:
                segment.append(token.text)
                segment_data.append({
                    'text': token.text,
                    'lemma': token.lemma_,
                    'pos': token.pos_,
                    'tag': token.tag_,
                    'dep': token.dep_,
                    'shape': token.shape_,
                    'is_alpha': token.is_alpha,
                    'is_stop': token.is_stop
                })

    if segment:
        segments.append({
            'text': ' '.join(segment),
            'details': segment_data
        })
    return segments

def process_text(text):
    doc = nlp(text)
    return get_segments(doc)

texts = df['review_full_text'].apply(lambda x: process_text(clean_text(x)))
texts.head()

/opt/conda/lib/python3.10/site-packages/cupy/cuda/compiler.py:233: PerformanceWarning: Jitify is performing a one-time only warm-up to populate the persistent cache, this may take a few seconds and will be improved in a future release...
  jitify._init_module()


KeyboardInterrupt: 

# Применение NLP моделей

In [ ]:
from transformers import pipeline
import numpy as np

classifier = pipeline('text-classification', model='bert-base-uncased')
def classify_text(text):
    result = classifier(text)
    return result[0]['label']

def analyze_text(text):
    sentiment = classify_text(text)
    return sentiment

texts['sentiment'] = texts['text'].apply(lambda x: analyze_text(x))
texts.head()